In [19]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf
import mnist
import copy, re
import scipy
import scipy.misc
from matplotlib import pyplot as plt


In [47]:
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)


Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [52]:
input_layer = tf.reshape(train_data[0:100], [100, 28, 28, 1])
input_layer

<tf.Tensor 'Reshape_11:0' shape=(100, 28, 28, 1) dtype=float32>

In [53]:
conv1 = tf.layers.conv2d(
    inputs=input_layer,
    filters=32,
    kernel_size=[5, 5],
    padding="same",
    activation=tf.nn.relu)
conv1

<tf.Tensor 'conv2d_6/Relu:0' shape=(100, 28, 28, 32) dtype=float32>

In [54]:
pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
pool1

<tf.Tensor 'max_pooling2d_3/MaxPool:0' shape=(100, 14, 14, 32) dtype=float32>

In [55]:
conv2 = tf.layers.conv2d(
    inputs=pool1,
    filters=64,
    kernel_size=[5, 5],
    padding="same",
    activation=tf.nn.relu)

pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
pool2

<tf.Tensor 'max_pooling2d_4/MaxPool:0' shape=(100, 7, 7, 64) dtype=float32>

In [56]:
pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)


In [57]:
dropout = tf.layers.dropout(
    inputs=dense, rate=0.4, training=True )

In [58]:
logits = tf.layers.dense(inputs=dropout, units=10)
logits

<tf.Tensor 'dense_4/BiasAdd:0' shape=(100, 10) dtype=float32>

In [59]:
predictions = {
    "classes": tf.argmax(input=logits, axis=1),
    "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
}
predictions["classes"]

<tf.Tensor 'ArgMax_5:0' shape=(100,) dtype=int64>

In [60]:
onehot_labels = tf.one_hot(indices=tf.cast(train_labels[0:100], tf.int32), depth=10)
loss = tf.losses.softmax_cross_entropy(
    onehot_labels=onehot_labels, logits=logits)

In [62]:
optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
train_op = optimizer.minimize(loss=loss, global_step=tf.train.get_global_step())
train_estimator = tf.estimator.EstimatorSpec(mode=tf.estimator.ModeKeys.TRAIN, loss=loss, train_op=train_op)

In [72]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

### Training Classifier 

In [73]:
mnist_classifier = tf.estimator.Estimator( model_fn = cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x18285bf0b8>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [74]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

In [75]:
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.0849629  0.11714421 0.11573903 0.09909444 0.08740583 0.09572533
  0.10743641 0.10316499 0.09775116 0.09157573]
 [0.08179388 0.10420158 0.11044066 0.09908716 0.09205507 0.09991898
  0.11797932 0.09809    0.09449134 0.10194201]
 [0.10353641 0.09889112 0.10463064 0.11138341 0.09715366 0.08207294
  0.09816812 0.09394033 0.10802936 0.10219399]
 [0.09939157 0.10834882 0.11074917 0.10216114 0.08725474 0.09530064
  0.10706915 0.10868237 0.10594466 0.07509778]
 [0.10010748 0.10410996 0.10418529 0.09704039 0.08655524 0.1036218
  0.10537529 0.10219982 0.10427659 0.09252815]
 [0.08597376 0.10258823 0.11031584 0.09680036 0.08358523 0.11186144
  0.12

INFO:tensorflow:loss = 2.3168242, step = 1
INFO:tensorflow:probabilities = [[0.09760415 0.10473936 0.10749077 0.09858597 0.0845237  0.10965111
  0.10867858 0.10400099 0.09183907 0.09288634]
 [0.08269434 0.1052414  0.10202894 0.10520633 0.09664083 0.10510761
  0.1019398  0.10179156 0.11042964 0.0889195 ]
 [0.10498984 0.09126646 0.09663317 0.09576578 0.09117724 0.10082132
  0.11325206 0.10384575 0.1038545  0.09839391]
 [0.08959962 0.10056443 0.10003464 0.09595922 0.09203352 0.10135026
  0.12217516 0.10095344 0.10651412 0.09081559]
 [0.10253228 0.10457043 0.10492197 0.11142336 0.09734181 0.09644331
  0.1175604  0.08740875 0.09351441 0.08428334]
 [0.08976714 0.10087592 0.09954821 0.11280712 0.09864483 0.1200802
  0.09949375 0.09361923 0.09781716 0.08734649]
 [0.08721322 0.10128855 0.11228582 0.1004038  0.08611517 0.10076308
  0.10651954 0.09955796 0.1085161  0.09733681]
 [0.09262003 0.10068008 0.10314418 0.09114907 0.10029226 0.09452145
  0.10695069 0.10589117 0.10402133 0.10072976]
 [0.07

INFO:tensorflow:global_step/sec: 2.7521
INFO:tensorflow:probabilities = [[0.09897123 0.09787051 0.11128711 0.09677452 0.09172557 0.10106875
  0.10969024 0.09326119 0.10098009 0.09837079]
 [0.09793132 0.10011618 0.10164369 0.11613664 0.09068561 0.10370804
  0.10634813 0.0877495  0.10139297 0.09428794]
 [0.10131457 0.08554587 0.10418134 0.102581   0.09898377 0.10239461
  0.11187173 0.09472692 0.09788059 0.1005196 ]
 [0.10341184 0.10558549 0.0930163  0.10761262 0.0901587  0.09074014
  0.12073267 0.10866206 0.08495799 0.09512218]
 [0.08030412 0.09902717 0.1021999  0.09840351 0.09483331 0.09798867
  0.1308206  0.10269941 0.10434718 0.08937617]
 [0.08484862 0.09509545 0.10663523 0.09857026 0.09612677 0.10319395
  0.11896139 0.09906123 0.0990418  0.09846532]
 [0.08608021 0.09317446 0.09569471 0.09617489 0.09985776 0.09169194
  0.13915105 0.10839317 0.10001051 0.0897713 ]
 [0.0842573  0.09586338 0.10721    0.12025994 0.10089663 0.09153815
  0.1110103  0.10483845 0.09835878 0.08576708]
 [0.0964

INFO:tensorflow:loss = 2.292661, step = 101 (36.332 sec)
INFO:tensorflow:probabilities = [[0.09730422 0.09588296 0.11401621 0.09599529 0.08462834 0.11062089
  0.10821328 0.09574251 0.10015258 0.0974438 ]
 [0.09084564 0.08778794 0.09512821 0.10507513 0.08974221 0.107305
  0.11529127 0.11600498 0.09976768 0.09305194]
 [0.10547769 0.09435087 0.10132951 0.09175794 0.09188272 0.09981637
  0.11659382 0.09957897 0.10615909 0.09305298]
 [0.09136574 0.09485278 0.0874683  0.10588577 0.10480028 0.10436551
  0.09365022 0.10164366 0.11486362 0.10110415]
 [0.1011496  0.09313609 0.10154981 0.10191544 0.08754105 0.1019283
  0.12523568 0.09857407 0.09913072 0.08983929]
 [0.10187755 0.09915399 0.09505495 0.09605721 0.08877391 0.10537744
  0.10761926 0.10385254 0.11261117 0.08962207]
 [0.0974728  0.09732211 0.11725927 0.09292803 0.09460932 0.1022106
  0.09338485 0.10648195 0.10684451 0.0914866 ]
 [0.0855089  0.0889347  0.10749309 0.09145453 0.0880357  0.1044323
  0.11986437 0.11026661 0.10555189 0.098457

INFO:tensorflow:global_step/sec: 2.98881
INFO:tensorflow:probabilities = [[0.10159469 0.09633498 0.09980083 0.10511879 0.09948245 0.09627801
  0.10959467 0.0892453  0.10864142 0.09390876]
 [0.09789477 0.08140977 0.1080002  0.10461196 0.09245492 0.10367129
  0.12290844 0.10032126 0.09110516 0.09762225]
 [0.09307257 0.09651525 0.11129989 0.10920778 0.09020761 0.09432361
  0.10693615 0.10425153 0.10326757 0.09091802]
 [0.09039225 0.09436047 0.10899332 0.09553692 0.10329702 0.08781201
  0.11522079 0.10028898 0.1047718  0.09932638]
 [0.09417422 0.08198015 0.10850919 0.11056607 0.10669006 0.10577866
  0.10283109 0.10521581 0.08958517 0.09466959]
 [0.0909791  0.10318218 0.09971226 0.10957702 0.09630182 0.10123064
  0.11222536 0.08882412 0.10149214 0.09647534]
 [0.09695547 0.09799228 0.11439421 0.09950687 0.08878095 0.09841483
  0.10507382 0.10263332 0.10504388 0.09120435]
 [0.10015    0.09321576 0.09491261 0.0919394  0.08393157 0.10931166
  0.1119135  0.09701473 0.12034901 0.09726182]
 [0.101

...

INFO:tensorflow:global_step/sec: 2.72242
INFO:tensorflow:probabilities = [[0.0000011  0.         0.00000036 0.00000015 0.9998375  0.0000089
  0.00000362 0.00000712 0.00000203 0.00013918]
 [0.00027439 0.00017896 0.00095352 0.00025663 0.00000833 0.00005894
  0.00003694 0.00008291 0.9977646  0.00038475]
 [0.00006639 0.00003275 0.00059645 0.00061943 0.00000376 0.00456945
  0.0000258  0.00000014 0.99408025 0.00000562]
 [0.00004189 0.00001212 0.00017056 0.00153303 0.00697683 0.00856897
  0.00000272 0.22258472 0.00121006 0.7588991 ]
 [0.0008878  0.0012059  0.00086175 0.39853263 0.00081102 0.2682104
  0.00001968 0.00264336 0.04494388 0.28188354]
 [0.00338427 0.00088164 0.00379503 0.00035969 0.00005153 0.01163141
  0.97978723 0.00000063 0.00010709 0.0000015 ]
 [0.00001476 0.99364895 0.00015125 0.00033736 0.00008177 0.00015005
  0.00046385 0.00008475 0.00499836 0.00006883]
 [0.0000035  0.00000004 0.00003551 0.00000366 0.99954647 0.00016508
  0.00007467 0.00006514 0.00007988 0.00002601]
 [0.00000

INFO:tensorflow:loss = 0.04920592, step = 19801 (36.738 sec)
INFO:tensorflow:probabilities = [[0.00001869 0.00696824 0.00003638 0.03628159 0.02178577 0.00104072
  0.00000591 0.02184672 0.00096328 0.9110526 ]
 [0.00002633 0.00010364 0.00091181 0.99583554 0.00000212 0.00285444
  0.00000336 0.00002877 0.00019706 0.00003697]
 [0.00000002 0.00001605 0.99958473 0.0003862  0.         0.00000576
  0.00000004 0.00000016 0.00000717 0.        ]
 [0.00000002 0.00000073 0.00000295 0.00002555 0.00000023 0.00000025
  0.         0.99993145 0.00000433 0.00003454]
 [0.00003001 0.00003571 0.00163288 0.00001004 0.00217556 0.00082263
  0.995145   0.00000425 0.00013764 0.00000621]
 [0.00199321 0.00104577 0.00014653 0.00006124 0.00012764 0.99053746
  0.00044316 0.00001652 0.00562682 0.00000166]
 [0.00000121 0.00000002 0.00000063 0.00000406 0.9462361  0.00081741
  0.00001476 0.000046   0.00261994 0.0502599 ]
 [0.00000065 0.00004383 0.99935144 0.00055419 0.00000027 0.00000508
  0.00000008 0.00003228 0.00001194

INFO:tensorflow:global_step/sec: 3.02653
INFO:tensorflow:probabilities = [[0.00001116 0.00001137 0.00081698 0.00001542 0.98559374 0.0116199
  0.0014342  0.00009775 0.00020124 0.00019826]
 [0.00048509 0.98979014 0.00297046 0.00029084 0.00008284 0.00000283
  0.00027956 0.00068923 0.00529661 0.00011241]
 [0.00027431 0.00000797 0.00059197 0.00000196 0.9902402  0.00340382
  0.00146679 0.00003244 0.00291126 0.00106925]
 [0.00019595 0.00000247 0.9988024  0.00042361 0.00000957 0.00000501
  0.00000787 0.00000029 0.0005425  0.00001029]
 [0.         0.00000243 0.00000058 0.9996846  0.         0.00030898
  0.         0.00000001 0.00000029 0.00000321]
 [0.00000106 0.         0.00000018 0.00000001 0.99950445 0.00000121
  0.00047916 0.00000038 0.0000052  0.00000843]
 [0.00023751 0.00000002 0.00002725 0.00196181 0.00000023 0.00078643
  0.00000003 0.00043197 0.99389595 0.0026588 ]
 [0.00040933 0.00001687 0.00306313 0.8637503  0.00000292 0.00079258
  0.00000028 0.00005816 0.12987894 0.00202754]
 [0.0000

INFO:tensorflow:loss = 0.139933, step = 19901 (33.030 sec)
INFO:tensorflow:probabilities = [[0.0000186  0.00000004 0.00016599 0.00000023 0.00036071 0.00006401
  0.99917656 0.00000001 0.00021332 0.00000034]
 [0.00007903 0.05765383 0.8048875  0.07057566 0.00015081 0.00093668
  0.00198407 0.06148722 0.00214553 0.00009975]
 [0.00013456 0.98410404 0.00154828 0.00324304 0.00217273 0.00011815
  0.0004629  0.0062284  0.00058572 0.00140216]
 [0.00000024 0.00039916 0.00032913 0.99842274 0.00000367 0.00007834
  0.00000012 0.00001262 0.00049679 0.00025721]
 [0.00000034 0.00000271 0.00007323 0.99957436 0.00000068 0.00000493
  0.         0.0000117  0.00001264 0.00031948]
 [0.00000049 0.00000151 0.00010091 0.00007993 0.00000444 0.00000517
  0.00000002 0.9995408  0.00000117 0.0002656 ]
 [0.00005032 0.00529655 0.00051435 0.00021279 0.00068788 0.00092295
  0.98721355 0.0000003  0.00510118 0.00000011]
 [0.00003623 0.00000019 0.00000584 0.00003311 0.00000468 0.00008436
  0.00000004 0.9962514  0.0000056  0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.12379668.


In [77]:

eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-25-21:54:14
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-25-21:54:26
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9681, global_step = 20000, loss = 0.10392269
{'accuracy': 0.9681, 'loss': 0.10392269, 'global_step': 20000}
